In [1]:
from libsvm.svmutil import *
import numpy as np
from sklearn.feature_extraction import DictVectorizer
from sklearn.metrics.pairwise import rbf_kernel


In [2]:
y, x = svm_read_problem('mnist.scale')
x

[{153: 0.0117647,
  154: 0.0705882,
  155: 0.0705882,
  156: 0.0705882,
  157: 0.494118,
  158: 0.533333,
  159: 0.686275,
  160: 0.101961,
  161: 0.65098,
  162: 1.0,
  163: 0.968627,
  164: 0.498039,
  177: 0.117647,
  178: 0.141176,
  179: 0.368627,
  180: 0.603922,
  181: 0.666667,
  182: 0.992157,
  183: 0.992157,
  184: 0.992157,
  185: 0.992157,
  186: 0.992157,
  187: 0.882353,
  188: 0.67451,
  189: 0.992157,
  190: 0.94902,
  191: 0.764706,
  192: 0.25098,
  204: 0.192157,
  205: 0.933333,
  206: 0.992157,
  207: 0.992157,
  208: 0.992157,
  209: 0.992157,
  210: 0.992157,
  211: 0.992157,
  212: 0.992157,
  213: 0.992157,
  214: 0.984314,
  215: 0.364706,
  216: 0.321569,
  217: 0.321569,
  218: 0.219608,
  219: 0.152941,
  232: 0.0705882,
  233: 0.858824,
  234: 0.992157,
  235: 0.992157,
  236: 0.992157,
  237: 0.992157,
  238: 0.992157,
  239: 0.776471,
  240: 0.713725,
  241: 0.968627,
  242: 0.945098,
  261: 0.313725,
  262: 0.611765,
  263: 0.419608,
  264: 0.992157,
 

In [3]:

def class_choices(x, y ,class_a, class_b):
    label_class = [] 
    feature_class = []
    nx = np.array(x)
    ny = np.array(y)
    new_set = (ny  == class_a )| (ny == class_b)
    label_class = ny[new_set]
    feature_class = nx[new_set]
    # for label  in range(len(y)) :
    #     if y[label] == class_a or y[label] == class_b :
    #         label_class.append(y[label])
    #         feature_class.append(x[label])
    label_class = np.where(label_class == class_a, 1, -1)

    # return np.array(label_class) , np.array(feature_class)
    return label_class , feature_class
            
label_class ,feature_class = class_choices(x ,y ,class_b = 7 , class_a = 3)
 
print(label_class[:20])
print(feature_class[:10])


[ 1  1  1 -1  1 -1  1 -1 -1  1  1  1 -1 -1  1 -1 -1  1 -1 -1]
[{152: 0.14902, 153: 0.168627, 154: 0.411765, 155: 1.0, 156: 0.992157, 157: 0.992157, 158: 0.992157, 159: 0.992157, 160: 0.992157, 161: 0.682353, 162: 0.0235294, 178: 0.168627, 179: 0.545098, 180: 0.878431, 181: 0.886275, 182: 0.988235, 183: 0.992157, 184: 0.988235, 185: 0.988235, 186: 0.988235, 187: 0.988235, 188: 0.988235, 189: 0.988235, 190: 0.619608, 191: 0.054902, 206: 0.698039, 207: 0.988235, 208: 0.988235, 209: 0.988235, 210: 0.988235, 211: 0.992157, 212: 0.988235, 213: 0.988235, 214: 0.988235, 215: 0.988235, 216: 0.988235, 217: 0.988235, 218: 0.988235, 219: 0.231373, 234: 0.427451, 235: 0.988235, 236: 0.988235, 237: 0.901961, 238: 0.517647, 239: 0.521569, 240: 0.517647, 241: 0.517647, 242: 0.741176, 243: 0.988235, 244: 0.988235, 245: 0.988235, 246: 0.988235, 247: 0.231373, 262: 0.0156863, 263: 0.113725, 264: 0.113725, 265: 0.0941176, 270: 0.054902, 271: 0.886275, 272: 0.988235, 273: 0.988235, 274: 0.67451, 275: 0.027

In [ ]:
C = [0.1,1,10]
Y = [0.1,1,10]
result = {}
def squared_distance(x1, x2):
    keys = set(x1.keys()).union(set(x2.keys()))
    return sum((x1.get(k, 0) - x2.get(k, 0)) ** 2 for k in keys)

for i in Y:
    for j in C:
            prob  = svm_problem(label_class, feature_class, isKernel=False)
            parameter = svm_parameter(f'-s 0 -t 2 -g {i} -c {j} -q')  

            model = svm_train(prob, parameter)
            sv_indices = model.get_sv_indices()  
            alphas = model.get_sv_coef()  
            print(alphas)
            sv_indices_zero_based = [idx - 1 for idx in sv_indices]#
            y_sv = np.array([label_class[idx] for idx in sv_indices_zero_based])  #基於sv 所對應的label 
            x_sv = [feature_class[idx] for idx in sv_indices_zero_based]  
            print(x_sv[:30])
            w_squared = 0
            num_sv = len(alphas) # includ all alpha = 0 slow
            for r in range(num_sv):
                for k in range(num_sv):
                    xi = x_sv[r]
                    xj = x_sv[k]
                    yi = y_sv[r]
                    yj = y_sv[k]
                    ai = alphas[r][0]# 理論沒有 0因爲 xy 是基於suport vector
                    aj = alphas[k][0]
                    k_ij = np.exp(-i * squared_distance(xi, xj))
                    w_squared += ai * aj * yi * yj * k_ij
            #算 w 倒數
            margin = 1 / np.sqrt(w_squared)
            
            #字典
            result[(j, i)] = margin
            
            print(f'C={j}, gamma={i}, Margin={margin}')
        
 

Exception ignored on calling ctypes callback function: <function print_null at 0x0000024016C60FE0>
Traceback (most recent call last):
  File "c:\Users\cheeh\anaconda3\Lib\site-packages\libsvm\svm.py", line 58, in print_null
    def print_null(s):
    
KeyboardInterrupt: 


[(0.04148516146450055,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.01475429442530313,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.09509912204947932,), (0.1,), (0.1,), (0.03801290927536447,), (0.1,), (0.04392794690785232,), (0.1,), (0.038642280048188316,), (0.1,), (0.09732220755811767,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.013803995694278544,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.01821859065797816,), (0.1,), (0.04999907894238565,), (0.1,), (0.07070525932191207,), (0.1,), (0.054954729374796146,), (0.1,), (0.1,), (0.0728846562153057,), (0.1,), (0.1,), (0.1,), (0.1,), (0.0674851511431411,), (0.1,), (0.09000229560653837,), (0.09913239594890305,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.022763939044744677,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.023036768601364197,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1

In [ ]:
C = [0.1,1,10]
Y = [0.1,1,10]
result = {}
# 初始化 DictVectorizer
vectorizer = DictVectorizer(sparse=False)  # 使用密集數組

# 定義 squared_distance 函數（如果需要）
def squared_distance_numpy(x1, x2):
    return np.sum((x1 - x2) ** 2)

for i in Y:
    for j in C:
            prob  = svm_problem(label_class, feature_class, isKernel=False)
            parameter = svm_parameter(f'-s 0 -t 2 -g {i} -c {j} -q')  

            model = svm_train(prob, parameter)
            sv_indices = model.get_sv_indices()  
            alphas = model.get_sv_coef()  
            print(alphas)
            sv_indices_zero_based = [idx - 1 for idx in sv_indices]#
            y_sv = np.array([label_class[idx] for idx in sv_indices_zero_based])  #基於sv 所對應的label 
            x_sv = [feature_class[idx] for idx in sv_indices_zero_based]  
            X_sv_dense = vectorizer.fit_transform(x_sv)  # 形狀為 (N_SV, n_features)
            
            # 計算 RBF 核矩陣
            K_sv = rbf_kernel(X_sv_dense, X_sv_dense, gamma=i)  # 形狀為 (N_SV, N_SV)
            
            # 展平 alphas
            alphas_flat = np.array(alphas).flatten()  # 形狀為 (N_SV,)
            
            # 計算 alpha * y
            alpha_y = alphas_flat * y_sv  #same 是 (N_SV,)
            
            # 計算 ||w||^2
            w_squared = alpha_y @ K_sv @ alpha_y  # scalar 
            
          
            margin = 1 / np.sqrt(w_squared)
            
            # 打印結果
            print(f'C={j}, gamma={i}, Margin={margin}')
        
           

[(0.04148516146450055,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.01475429442530313,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.09509912204947932,), (0.1,), (0.1,), (0.03801290927536447,), (0.1,), (0.04392794690785232,), (0.1,), (0.038642280048188316,), (0.1,), (0.09732220755811767,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.013803995694278544,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.01821859065797816,), (0.1,), (0.04999907894238565,), (0.1,), (0.07070525932191207,), (0.1,), (0.054954729374796146,), (0.1,), (0.1,), (0.0728846562153057,), (0.1,), (0.1,), (0.1,), (0.1,), (0.0674851511431411,), (0.1,), (0.09000229560653837,), (0.09913239594890305,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.022763939044744677,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.023036768601364197,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1,), (0.1